## library loading

In [1]:
import pandas as pd # 판다스 
import numpy as np # 넘파이
import glob # 파일 여러개 불러올 때
import time, datetime
from datetime import datetime

import re # 정규표현식

## Load data 

In [ ]:
# Inven Data 

df1 = pd.read_csv("data/invenData_1~10000.csv", encoding = 'utf8', header=None, engine='python')
df2 = pd.read_csv("data/invenData_10001~50000.csv", encoding='utf8', header=None, engine='python')
df3 = pd.read_csv("data/invenData_50001~70000.csv", encoding='utf8', header=None, engine='python')
df4 = pd.read_csv("data/invenData_70001~85834.csv", encoding='utf8', header=None, engine='python')
df5 = pd.read_csv("data/invenData_85835~100000.csv", encoding='utf8', header=None, engine='python')
df6 = pd.read_csv("data/invenData_100001~120000.csv", encoding='utf8', header=None, engine='python')
df7 = pd.read_csv("data/invenData_120001~140000.csv", encoding='utf8', header=None, engine='python')
df8 = pd.read_csv("data/invenData_140001~152823.csv", encoding='utf8', header=None, engine='python')
df9 = pd.read_csv("data/invenData_152824~160100.csv", encoding='utf8', header=None, engine='python')

In [2]:
# Battlenet Data
df10 = pd.read_csv("data/battlenetData.csv", encoding='utf8', header=None, engine='python')

In [3]:
df10.tail()

0           1                   2                       3  \
5695  4564440767         카라딘  2017.04.06 03시 28분  발리라보고 데자뷰 느끼는 사람 없습니까?   
5696  4564493860          공격  2017.04.22 03시 08분      지금 ptr 게임이 안되는거같은데   
5697  4564503573      고만하고자라  2017.04.22 02시 49분             가기전에 의견만남김.   
5698  4564493427       Messi  2017.04.21 20시 58분         게임 미참여로 정지 먹었는데   
5699  4564503257  geschichte  2017.04.21 19시 25분      한사람 나가면 게임무효를 시켜야지   

                                                      4  
5695  [빠대같은 초보존에선 종결 급 양학을 하고 다니면서 카운터를 준비할 수 있는 등급전...  
5696  [서버가 게임 생성에 실패하였습니다 뜨면서 게임이안되요.. 저만그런거같지않는데. 공...  
5697  [히오스 오픈베타때부터 해온사람으로서 몇자적고간다.트롤,탈주자,겜말아먹는넘들 단속안...  
5698                        [날짜가 지나도 안풀리네요. 영구정지먹은건가요?]  
5699  [빨리 끝나라고 가만히 있자니 튕기고..계속하자니 어차피 질 게임 시간만 길어지고 ...

## Data preprocessing - Battlenet

In [4]:
# 배틀넷 데이터부터 전처리 준비
df10.columns = ['link_id', 'user_id', 'timestamp', 'title', 'contents']

### 시간 데이터 전처리

In [5]:
type(df10['timestamp'])

pandas.core.series.Series

In [6]:
df10.iloc[1,3]

'매칭 시스템, 아무리 생각해도 문제가 많습니다'

In [7]:
df10 = df10[df10['timestamp'].notnull()]

In [8]:
df10[1017:1018]

link_id user_id           timestamp               title  \
1018  4566519476   페텔기우스  2018.06.03 04시 59분  겐지 E이동거리만 30% 줄이자.   

                                               contents  
1018  [겐지를 막 개 너프하라거나 그런소리 안한다.단지 e가 쿨초기화에 이것저것 좋은것들...

index 1017번째 글은 비어있어서 드랍함.

In [9]:
# 글을 드랍하였기 떄문에 인덱스 리셋

df10.reset_index(inplace=True)

In [10]:
# 새로운 데이트타임 형식 만들기

new_dates = []

for i in range(5699):
    
    years = int(df10['timestamp'][i][0:4])
    months = int(df10['timestamp'][i][5:7])
    days = int(df10['timestamp'][i][8:10])
    hours = int(df10['timestamp'][i][11:13]) 
    minutes = int(df10['timestamp'][i][15:17])
    
    dates = datetime(years, months, days, hours, minutes)
    
    new_dates.append(dates)

In [11]:
df10["new_datetime"] = new_dates

In [12]:
df10.drop('timestamp',axis=1, inplace=True)

In [13]:
df10.head()

index     link_id   user_id                              title  \
0      0  4564557252  비전력이부조카당               아바투르 유저인데, 하나 건의합니다.   
1      1  4567016696     네이팜데쓰          매칭 시스템, 아무리 생각해도 문제가 많습니다   
2      2  4567016695     souse                    ㅈ같은 매칭좀 어캐좀 해봐요   
3      3  4567026707      Best                          아나 스킨관련..   
4      4  4567036673        세월  5인팟 + 승률50%집착매칭 + 밸런스 파괴 = 빠대무간지옥   

                                            contents        new_datetime  
0  [아바투르 유저인데, 하나 건의합니다.새로 생긴 하나무라 맵...뭐 이것도 맵 자체... 2017-05-06 05:21:00  
1  [매칭좀 제대로 해주세요.9연패가 말이 되는 처사입니까 며칠전에 16연승했다고 벌을... 2018-09-08 16:53:00  
2  [왜 내가 잘해도 ㅈ같이못하는 새키들때문에 게임을 져야하죠? 왜 심지어 못하는새키랑... 2018-09-08 16:22:00  
3  [신 스킨 살무사 아나 수면총 색 고정말고.  스킨 색 대로 해주셧으면 좋겠습니다.... 2018-09-08 15:13:00  
4  [승률 50% 만든다고 조합 !@내놓고5인팟은 여전히 솔팟 사이에서 개판치고다니고너... 2018-09-07 13:58:00

### 그 외 중복 데이터 처리하기

In [14]:
# 블리자드 사에서 올린 공지는 제외

df10 = df10[df10.user_id != "Blizzard Entertainment"]

In [15]:
# 글 완전 중복인 사람 파악하기

df10['contents'].drop_duplicates(keep='first')

0       [아바투르 유저인데, 하나 건의합니다.새로 생긴 하나무라 맵...뭐 이것도 맵 자체...
1       [매칭좀 제대로 해주세요.9연패가 말이 되는 처사입니까 며칠전에 16연승했다고 벌을...
2       [왜 내가 잘해도 ㅈ같이못하는 새키들때문에 게임을 져야하죠? 왜 심지어 못하는새키랑...
3       [신 스킨 살무사 아나 수면총 색 고정말고.  스킨 색 대로 해주셧으면 좋겠습니다....
4       [승률 50% 만든다고 조합 !@내놓고5인팟은 여전히 솔팟 사이에서 개판치고다니고너...
5       [대만인 새끼들좀 매칭 안되게 해라.말도 안통하는 머저리 새끼들하고 왜 해야하는건데...
6       [신영웅 이제 그만좀만드시고요. 기존영웅 쓸수나있게 손좀보시죠^^ 뭐가 더 급한건지...
7       [삭제가 답이지 죽광도 리메이크해도 망맵 하나무라도 리메이크해도 망맵블랙하트는 예전...
8       [HOTS는 이전부터 영웅리그에 대한 문제가 많았습니다.크게 정리하자면 4가지가 있...
9       [분명 픽창에서는 제가 하고싶은 영웅을 선택했는데 시작하고나면 다른영웅으로 시작이됩...
10      [1년 한걸로 아는데 그래서 재밌음?이것만큼 강제한타맵은 없을 것 같은데 적어도 빠...
11      [진짜 개빡친다 7연패하고 2승하고 다시 7연패가 말이되냐?옛날에 승률올려놓은거 때...
12      [영웅과 스킨, 탈것 까지는 제대로 표기되지만, 예를 들어 미확인 이모티콘이 하나 ...
13      [영웅리그에서 적팀에 트위치 스트리머 '뱅붕'을 의식하고, 아군 팀에서 계속 트롤하...
14                      [화이트메인 힐량이 게임내 플레이 중 혐오감을 조장합니다.]
15      [ㄹㅇ 이따위로 디자인 할꺼면 걍 이겜 롤 오브 더 스톰으로 바꾸셈영웅 특색은 씨1...
16      [ㅈ까 씨.발 저렇게 종횡무진 전장 휩쓸고 다니는 걸 어떻게 쳐 잡아? 이러다가 나...
17      [힐러가 탱

In [16]:
# 헤비유저 파악 혹은 글 연달아 올린 사람 파악하기

user_list = df10['user_id'].unique()

for uid in user_list[:15]:
    dfuid = df10[df10['user_id']==uid]
    print(dfuid.iloc[:,[1,2,3,5]])

    

# 전처리 되도록이면 판다스로 하기. 유저 아이디 중복을 찾은다음에. 시간 차이가 몇 안나는 것들은 빼기(몇 분 이상 차이나면 없애는 방향으로)

         link_id   user_id                         title        new_datetime
0     4564557252  비전력이부조카당          아바투르 유저인데, 하나 건의합니다. 2017-05-06 05:21:00
3638  4565216710  비전력이부조카당  왜 히오스는 '최근 같이 플레이한 목록'이 없나요? 2017-09-14 07:19:00
      link_id user_id                      title        new_datetime
1  4567016696   네이팜데쓰  매칭 시스템, 아무리 생각해도 문제가 많습니다 2018-09-08 16:53:00
      link_id user_id            title        new_datetime
2  4567016695   souse  ㅈ같은 매칭좀 어캐좀 해봐요 2018-09-08 16:22:00
         link_id user_id          title        new_datetime
3     4567026707    Best      아나 스킨관련.. 2018-09-08 15:13:00
68    4566996719    Best             건의 2018-09-05 03:46:00
2627  4565604050    Best             빠대 2017-12-28 14:30:00
2660  4565614129    Best       한조 너프건의안 2017-12-26 01:18:00
2970  4565435532    Best  지원가 너프에 관하여.. 2017-11-30 04:36:00
3086  4565398541    Best      소냐 너프 건의안 2017-11-18 15:03:00
4237  4564767573    Best             빠대 2017-06-19 07:04:00
4583  4564622970    Best         

In [17]:
# 헤비 유저(빅마우스)들 (상위 10명)
print(user_list[0:10])

['비전력이부조카당' '네이팜데쓰' 'souse' 'Best' '세월' 'Ditto' 'JELAWAT' '요우몽' '파워디지몬'
 '인생이지겨워']


In [18]:
df10[df10['link_id']==4566866705]

index     link_id user_id              title  \
109    109  4566866705     요우몽  화메 궁쿨 책정부터 잘못되어있음   

                                              contents        new_datetime  
109  [성스러운징벌이 100초 붉은가호가 1분인데 @%*!!# 성능 따져봐도 당연 붉은가... 2018-08-30 04:10:00

In [19]:
df10[df10['link_id']==4566857028]

index     link_id user_id         title  \
189    189  4566857028   파워디지몬  HOTS 영웅리그 건의   

                                              contents        new_datetime  
189  [HOTS는 이전부터 영웅리그에 대한 문제가 많았습니다.크게 정리하자면 3가지가 있... 2018-08-21 06:01:00

In [20]:
# 위에서 나온 결과를 기준으로 판단하여 중복 행 몇개를 삭제한다. - 뒷 인덱스를 삭제합니다. 새로 쓴 글이 의사를 더 잘 반영한다고 기준을 둠

df10.drop([189],inplace=True)
df10.drop([109],inplace=True)

In [21]:
df10.reset_index(inplace=True)

In [22]:
df10.tail()

level_0  index     link_id     user_id                   title  \
5635     5694   5695  4564440767         카라딘  발리라보고 데자뷰 느끼는 사람 없습니까?   
5636     5695   5696  4564493860          공격      지금 ptr 게임이 안되는거같은데   
5637     5696   5697  4564503573      고만하고자라             가기전에 의견만남김.   
5638     5697   5698  4564493427       Messi         게임 미참여로 정지 먹었는데   
5639     5698   5699  4564503257  geschichte      한사람 나가면 게임무효를 시켜야지   

                                               contents        new_datetime  
5635  [빠대같은 초보존에선 종결 급 양학을 하고 다니면서 카운터를 준비할 수 있는 등급전... 2017-04-06 03:28:00  
5636  [서버가 게임 생성에 실패하였습니다 뜨면서 게임이안되요.. 저만그런거같지않는데. 공... 2017-04-22 03:08:00  
5637  [히오스 오픈베타때부터 해온사람으로서 몇자적고간다.트롤,탈주자,겜말아먹는넘들 단속안... 2017-04-22 02:49:00  
5638                        [날짜가 지나도 안풀리네요. 영구정지먹은건가요?] 2017-04-21 20:58:00  
5639  [빨리 끝나라고 가만히 있자니 튕기고..계속하자니 어차피 질 게임 시간만 길어지고 ... 2017-04-21 19:25:00

In [23]:
df10.iloc[2,5]

"[왜 내가 잘해도 ㅈ같이못하는 새키들때문에 게임을 져야하죠? 왜 심지어 못하는새키랑 또 같은판되서 강등전까지 끌고가죠? 매칭시스템 내가 4년동안 블리자드 히오스 개사랑햇는데 요즘은 인성파탄나고 심한욕까지 하게되었습니다.이제 애정도 식을 지경입니다. 얼마나 더 매칭 밸런스 시스템을 ㅈ같이 해야 합니까 다이긴 게임  던지는 새키들 보면 죽여버리고싶은욕구까지 드는데'나의 4년간의 사랑이 올해 다 식어 갑니다.%!%!!!]"

### 데이터 불용어 전처리

In [24]:
p_http = re.compile("(((http(s?))\:\/\/)?)([0-9a-zA-Z\-]+\.)+[a-zA-Z]{2,6}(\:[0-9]+)?(\S*)")
p_char = re.compile("[^가-힣ㄱ-ㅎㅏ-ㅣa-zA-Z0-9ㅣ ]")
p_tag = re.compile("<.+>")
p_brac = re.compile("[[\]]")

In [25]:
def patternRemover(doc):
    doc = p_http.sub(' ', doc)
    doc = p_char.sub(' ', doc)
    doc = p_tag.sub('', doc)
    doc = p_brac.sub('', doc)
    return doc

In [26]:
for i in range(len(df10["contents"])):
    df10.iloc[i,5] = patternRemover(df10.iloc[i,5])

In [32]:
df10[5000:5001]

level_0  index     link_id user_id                  title  \
5000     5057   5058  4564607018     세이카  히오스 밸런스패치에 대한 개인적인 요구   

                                               contents        new_datetime  
5000   현재 무빙캐릭터로 인한 밸런스문제가 적잖아 있다고 생각함 루시우를 제외한 모든 무... 2017-05-12 11:42:00

In [33]:
df10

level_0  index     link_id     user_id  \
0           0      0  4564557252    비전력이부조카당   
1           1      1  4567016696       네이팜데쓰   
2           2      2  4567016695       souse   
3           3      3  4567026707        Best   
4           4      4  4567036673          세월   
5           5      5  4567026700       Ditto   
6           6      6  4567046681     JELAWAT   
7           7      7  4567006799         요우몽   
8           8      8  4567036686       파워디지몬   
9           9      9  4567036678      인생이지겨워   
10         10     10  4567016679        LEoN   
11         11     11  4567026689       텔라마피아   
12         12     12  4567026688         계명성   
13         13     13  4567026687        온슈타인   
14         14     14  4567036675         김용현   
15         15     15  4567046672   FrostyDog   
16         16     16  4567026684         Age   
17         17     17  4567006798       랑게르한스   
18         18     18  4567026681     JELAWAT   
19         19     19  4566986780      니시즈미미호   
20         20     20  4567036670      BRPARK   
21         21     21  4567016666       존재감만땅   
22         22     22  4567026659        동백장군   
23         23     23  4567046661         신고산   
24         24     24  4567016657      Hermes   
25         25     25  4567006777   Sinabeuro   
26         26     26  4567026657        모이라이   
27         27     27  4566976739      냉동바퀴벌레   
28         28     28  4567006797        갈치갈치   
29         29     29  4566996758         요우몽   
...       ...    ...         ...         ...   
5610     5669   5670  4564505196        meze   
5611     5670   5671  4564494670        CroA   
5612     5671   5672  4564481552          오베   
5613     5672   5673  4564514986    주님한놈더갑니다   
5614     5673   5674  4564514731     Bastion   
5615     5674   5675  4564483194     cheater   
5616     5675   5676  4564514478  geschichte   
5617     5676   5677  4564514409        CroA   
5618     5677   5678  4564514402        CroA   
5619     5678   5679  4564504525         저항몬   
5620     5679   5680  4564482455     DTworld   
5621     5680   5681  4564482452         메오후   
5622     5681   5682  4564482451       zujak   
5623     5682   5683  4564514332      Cosmos   
5624     5683   5684  4564514290    디모엘리스는사랑   
5625     5684   5685  4564494456          셜록   
5626     5685   5686  4564514177        ZASK   
5627     5686   5687  4564387780      Shrimp   
5628     5687   5688  4564504099         소스바   
5629     5688   5689  4564503916         드립슈   
5630     5689   5690  4564513784       duroa   
5631     5690   5691  4564374159        짐래이너   
5632     5691   5692  4564476741         재쭈닝   
5633     5692   5693  4564508350    niceobha   
5634     5693   5694  4564486743     BoBTong   
5635     5694   5695  4564440767         카라딘   
5636     5695   5696  4564493860          공격   
5637     5696   5697  4564503573      고만하고자라   
5638     5697   5698  4564493427       Messi   
5639     5698   5699  4564503257  geschichte   

                                  title  \
0                  아바투르 유저인데, 하나 건의합니다.   
1             매칭 시스템, 아무리 생각해도 문제가 많습니다   
2                       ㅈ같은 매칭좀 어캐좀 해봐요   
3                             아나 스킨관련..   
4     5인팟 + 승률50%집착매칭 + 밸런스 파괴 = 빠대무간지옥   
5                        영웅리그 매칭에서 대만인들   
6                신영웅 그만만들고 기존영웅 손좀보시죠^^   
7                   망한맵들은 리메이크가 답이 아니다    
8                          히오스 영웅리그 개선안   
9                         다른 영웅 선택되는 버그   
10                            하나무라 리메이크   
11                          매칭이 왜 이따구냐?   
12        수집품 내에서 미확인 목록의 숫자 표시가 밀리는 현상   
13    트위치 '뱅붕'의 시청자인 영웅리그 트롤유저를 제재해주세요.   
14                              화이트메인OP   
15               장애새끼들 란데 디자인 병신같이 바꿔놨네   
16                     역시 빗나가지 않는 신캐 버프   
17         화메 자힐너프3일 안에 안하면 히오스 운영자 암걸림   
18                    침묵인데 스킬사용하는 메피스토?   
19                       메피스토는 그냥 삭제해라    
20                               알타 상향좀   
21                           겐지좀 리메이크해요   
22                     역시 똥망겜은 어쩔수 없는듯. 

In [34]:
df10["contents"][1410]

' 솔직히 영리 듀오까지 허용해야한다고 생각하지 않냐 정상인 한 명만이라도 데리고 해야할거 아니냐개발자 니네들 진짜 영리 해보긴 해보냐   그영리 듀오들이 영리를 터트려서 개발팀도 들들 볶아지다가 저렇게 패치한검니다  영리하는 사람들 말로는 현제가 비교적 낫다고 하네요   영리 문제점은 픽 스왑이 불가능함 그리고 거지같은 티어 시스템 그게 문제임 '

## data concat

## Tokenizing

In [35]:
import MeCab

In [36]:
m = MeCab.Tagger('-d /usr/local/lib/mecab/dic/mecab-ko-dic')

In [37]:
from konlpy.tag import Mecab
mecab = Mecab()

In [117]:
tokens_check = []

for i in list(df10["contents"]):
    k = mecab.pos(i)
    tokens_check.append(k)

In [118]:
tokens_check

[[('아바투르', 'NNP'),
  ('유저', 'NNG'),
  ('인데', 'VCP+EC'),
  ('하나', 'NR'),
  ('건', 'NNBC'),
  ('의', 'JKG'),
  ('합니다', 'VV+EF'),
  ('새로', 'MAG'),
  ('생긴', 'VV+ETM'),
  ('하나무라', 'NNP'),
  ('맵', 'NNG'),
  ('뭐', 'IC'),
  ('이것', 'NP'),
  ('도', 'JX'),
  ('맵', 'NNG'),
  ('자체', 'NNG'),
  ('에', 'JKB'),
  ('할', 'VV+ETM'),
  ('말', 'NNG'),
  ('이', 'JKS'),
  ('많', 'VA'),
  ('지만', 'EC'),
  ('그게', 'NP+JKS'),
  ('글', 'NNG'),
  ('남기', 'VV'),
  ('는', 'ETM'),
  ('주', 'NNBC'),
  ('목적', 'NNG'),
  ('은', 'JX'),
  ('넘어가', 'VV'),
  ('겠', 'EP'),
  ('습니다', 'EF'),
  ('그런데', 'MAJ'),
  ('이', 'MM'),
  ('맵', 'NNG'),
  ('에서', 'JKB'),
  ('는', 'JX'),
  ('아바투르', 'NNP'),
  ('로', 'JKB'),
  ('는', 'JX'),
  ('화물', 'NNG'),
  ('을', 'JKO'),
  ('밀', 'VV+ETM'),
  ('수', 'NNB'),
  ('가', 'JKS'),
  ('없', 'VA'),
  ('어서', 'EC'),
  ('엄청', 'MAG'),
  ('민폐', 'NNG'),
  ('가', 'JKS'),
  ('되', 'VV'),
  ('네요', 'EC'),
  ('빠른', 'VA+ETM'),
  ('대전', 'NNP'),
  ('에서', 'JKB'),
  ('이', 'MM'),
  ('맵', 'NNG'),
  ('걸리', 'VV'),
  ('면', 'EC'),
  ('욕먹', 'VV'),
 

In [119]:
# 명사형 추출
tokens = []

for i in list(df10["contents"]):
    k = mecab.nouns(i)
    for j in range(len(k)):
        if len(k[j]) > 1:
            tokens.append(k[j])
        else:
            continue

In [124]:
tokens

['아바투르',
 '유저',
 '하나',
 '하나무라',
 '이것',
 '자체',
 '그게',
 '목적',
 '아바투르',
 '화물',
 '민폐',
 '대전',
 '일반',
 '등급',
 '고르지',
 '아바투르',
 '제한',
 '해결',
 '초갈',
 '상황',
 '발생',
 '이건',
 '아바투르',
 '매칭',
 '연패',
 '처사',
 '며칠',
 '연승',
 '건가요',
 '팀원',
 '적군',
 '플레이어',
 '매칭',
 '팀원',
 '적과',
 '히어로즈',
 '오브',
 '스톰',
 '캐리',
 '작용',
 '게임',
 '플레이어',
 '경험',
 '공유',
 '때문',
 '혼자',
 '성장',
 '캐리',
 '개념',
 '혼자',
 '딴짓',
 '팀원',
 '영향',
 '이야기',
 '초보자',
 '팀원',
 '게임',
 '게임',
 '레이팅',
 '유저',
 '공평',
 '처사',
 '플레이',
 '팀원',
 '때문',
 '연속',
 '패배',
 '실망감',
 '우리',
 '생각',
 '매칭',
 '승부',
 '승패',
 '허탈',
 '승부',
 '게임',
 '승부',
 '조합',
 '승패',
 '결정',
 '게임',
 '적군',
 '아군',
 '초보',
 '게임',
 '중국어',
 '닉네임',
 '승패',
 '게임',
 '제게',
 '공정',
 '세계',
 '아시아',
 '유저',
 '게임',
 '권리',
 '서로',
 '실력',
 '감탄',
 '승부',
 '패배',
 '아군',
 '책망',
 '상대',
 '실력',
 '감탄',
 '게임',
 '지금',
 '매칭',
 '시스템',
 '문제',
 '여러분',
 '시행착오',
 '믿음',
 '해결책',
 '모두',
 '히오스',
 '때문',
 '게임',
 '강등전',
 '매칭',
 '시스템',
 '동안',
 '블리자드',
 '히오스',
 '사랑',
 '요즘',
 '인성',
 '파탄',
 '정도',
 '지경',
 '매칭',
 '밸런스',
 '시스템',
 '게임',
 '욕구',
 '사랑',
 '

In [125]:
tokens_df = pd.DataFrame({"tokens":tokens})

In [126]:
tokens_df.head()

tokens
0   아바투르
1     유저
2     하나
3   하나무라
4     이것

In [133]:
len(tokens)

168706

### 해야 할 일 :

두글자 단어를 빼려다 각 토큰이 행마다 들어가버려서 조건문 달때 writerow? 같은게 있으면 그렇게 넣어야할듯. 오늘은 여기까지.

In [129]:
df10["tokens_contents"] = tokens

ValueError: Length of values does not match length of index

In [131]:
import gensim.corpora as corpora


In [ ]:
id2word = corpora.Dictionary(df["tokens_contents"])

In [132]:
id2word = corpora.Dictionary("tokens")

TypeError: doc2bow expects an array of unicode tokens on input, not a single string

In [ ]:
texts = df["tokens_contents"]

In [ ]:
corpus = [id2word.doc2bow(text) for text in texts]

print(corpus[:1])

In [ ]:
# Human readable format of corpus (term-frequency)
[[(id2word[id], freq) for id, freq in cp] for cp in corpus[:1]]

할 일
1. 글자 수가 1인 이하인걸 드랍한다